In [22]:
import pandas as pd
import os
from pathlib import Path

In [41]:
class Player():
    def __init__(self, id, name, elo_rating, elo_rank):
        self.id = id
        self.name = name
        self.elo_rating = elo_rating
        self.elo_rank = elo_rank


class Match():
    """
    Classe amb la informació d'un partit de singles.
    """
    def __init__(self, tourney_id, tourney_name, draw_size, tourney_level, tourney_date, match_num, score, best_of, round, winner_id, loser_id,):
        self.tourney_id = tourney_id 
        self.tourney_name = tourney_name
        self.draw_size = draw_size
        self.tourney_level = tourney_level # G, F, D, M, A, C, S
        self.tourney_date = tourney_date
        self.match_id = str(tourney_id) + str(match_num) # a match-specific identifier. Often starting from 1, sometimes counting down from 300, and sometimes arbitrary. 
        self.score = score
        self.best_of = best_of # 3 or 5 games
        self.round = round
        self.winner_id = winner_id
        self.loser_id = loser_id


class Tour():
    """
    Classe que conté una llista de tots els partits d'un tour, en principi un any sencer
    Un objecte Tour en principi equivaldrà a un fitxer atp_matches_year.csv
    """
    def __init__(self, matches:list[Match], players:dict[int, Player], ranking: dict[Player, int]) -> None:
        self.matches = matches 
        self.players = players
        self.ranking = ranking

    def update_elo_ratings(self, winner:Player, loser:Player) -> None: # a l'atp els ranquings d'actualitzen després de cada torneig, NO després de cada partit
        """
        Mètode per actualitzar els elo ratings dels jugadors d'un partit.
        """
        
        # TODO: Decidir d'on treiem els paràmetres, de moment fixats
        # TODO: Canviar l'score (Sw, Sl) perquè depengui del resultat del partit
        ksi = 400
        K = 40
        Sw = 1 
        Sl = 0

        # Algorisme per calcular elo-ratings
        old_wr = winner.elo_rating
        old_lr = loser.elo_rating

        d_w = old_wr - old_lr
        d_l = old_lr - old_wr

        mu_w = 1 / (1 + pow(10, -d_w/ksi))
        mu_l = 1 / (1 + pow(10, -d_l/ksi))

        # Actualitzar els valors dels elo-ratings dels jugadors.
        winner.elo_rating = round(old_wr + K*(Sw - mu_w), 3)
        loser.elo_rating = round(old_lr + K*(Sl - mu_l), 3)


    def update_elo_ranking(self, winner:Player, loser:Player):
        # Update Elo rating in the dictionary
        self.ranking[winner] = winner.elo_rating
        self.ranking[loser] = loser.elo_rating

        # Get the sorted list of players (keeping original order in a list to avoid re-sorting everyone)
        sorted_players = sorted(self.ranking.keys(), key=lambda p: self.ranking[p], reverse=True)

        # Update ranks only if necessary
        for new_rank, player in enumerate(sorted_players, start=1):
            if player.elo_rank != new_rank:
                player.elo_rank = new_rank  # Update player's rank


    def simulate_tour(self) -> None: 
        print(f'Simulating tour...\n {len(self.matches)} matches.')
        for match in self.matches:
            print(f'Simulating match {match.match_id}...')
            winner = self.players[match.winner_id]
            loser = self.players[match.loser_id]

            # TODO: Calcular aqui el score S

            self.update_elo_ratings(winner, loser)
            self.update_elo_ranking(winner, loser)

    def save_ranking(self) :
        """
        Guarda el ranking sencer un cop acabat el tour
        """
        print('hi')
        with open('ranking.txt', 'w') as f:
            f.write(f'{'Rank  Name':<25} {"Rating":>10}\n')  # Column headers with proper alignment
            
            for rank, (player, rating) in enumerate(sorted(self.ranking.items(), key=lambda item: item[1], reverse=True), start=1): 
                print(rank)
                f.write(f'{rank}.  {player.name:<25} {rating:>10}\n')
            

In [42]:

def load_tour_from_csv(file_path: str, tour: Tour = Tour(matches=[], players={}, ranking={})) -> Tour:
    """
    Reads a CSV file and creates a Tour object containing all matches.

    Args:
        file_path (str): Path to the CSV file.

    Returns:
        Tour: An instance of Tour containing a list of Match objects.
    """
    print(f'Loading matches from {file_path}')
    df = pd.read_csv(file_path)

    for _, row in df.iterrows():
        # Obtenir id dels dos jugadors del partit
        winner_id = row["winner_id"]
        loser_id = row["loser_id"]

        # Crear els jugadors si encara no existeixen
        if winner_id not in tour.players:
            tour.players[winner_id] = Player(winner_id, row["winner_name"], 0, None)  # Default ELO rating 0
        if loser_id not in tour.players:
            tour.players[loser_id] = Player(loser_id, row["loser_name"], 0, None)

        # Guardar la info del partit
        match = Match(
            tourney_id=row["tourney_id"],
            tourney_name=row["tourney_name"],
            draw_size=row["draw_size"],
            tourney_level=row["tourney_level"],
            tourney_date=row["tourney_date"],
            match_num=row["match_num"],
            score=row["score"],
            best_of=row["best_of"],
            round=row["round"],
            winner_id=winner_id,
            loser_id=loser_id,
        )

        tour.matches.append(match)

    return tour

def load_all_tours(folder_path: str = '/Users/FRIGO/Desktop/Escriptori (MacBook Air)/MATCAD/5e/TFG/tfg-elo-rating-main/data') -> Tour: 
    """
    Llegeix tots els fitxers de tours i crea un objecte Tour amb tots els partits de la carpeta 'folder_path'.

    Args: 
        folder_path (str): Ruta a la carpeta que conté els tots fitxers CSV.

    Returns: 
        Tour(): Un objecte Tour que conté tots els partits de la carpeta 'folder_path'.
    """

    mega_tour = Tour(matches=[], players={}, ranking={})
    
    for subdir, dirs, files in os.walk(Path(folder_path)):
        for file in sorted(files):
            if file.endswith('.csv'):
                file_path = os.path.join(subdir, file)
                mega_tour = load_tour_from_csv(file_path, tour=mega_tour)
    


    return mega_tour

In [25]:
all_tours = load_all_tours('data/atp_matches')

Loading matches from data/atp_matches/atp_matches_1968.csv
Loading matches from data/atp_matches/atp_matches_1969.csv
Loading matches from data/atp_matches/atp_matches_1970.csv
Loading matches from data/atp_matches/atp_matches_1971.csv
Loading matches from data/atp_matches/atp_matches_1972.csv
Loading matches from data/atp_matches/atp_matches_1973.csv
Loading matches from data/atp_matches/atp_matches_1974.csv
Loading matches from data/atp_matches/atp_matches_1975.csv
Loading matches from data/atp_matches/atp_matches_1976.csv
Loading matches from data/atp_matches/atp_matches_1977.csv
Loading matches from data/atp_matches/atp_matches_1978.csv
Loading matches from data/atp_matches/atp_matches_1979.csv
Loading matches from data/atp_matches/atp_matches_1980.csv
Loading matches from data/atp_matches/atp_matches_1981.csv
Loading matches from data/atp_matches/atp_matches_1982.csv
Loading matches from data/atp_matches/atp_matches_1983.csv
Loading matches from data/atp_matches/atp_matches_1984.c

In [26]:
all_tours.simulate_tour()

Simulating tour...
 194996 matches.
Simulating match 1968-2029270...
Simulating match 1968-2029271...
Simulating match 1968-2029272...
Simulating match 1968-2029273...
Simulating match 1968-2029274...
Simulating match 1968-2029275...
Simulating match 1968-2029276...
Simulating match 1968-2029277...
Simulating match 1968-2029278...
Simulating match 1968-2029279...
Simulating match 1968-2029280...
Simulating match 1968-2029281...
Simulating match 1968-2029282...
Simulating match 1968-2029283...
Simulating match 1968-2029284...
Simulating match 1968-2029285...
Simulating match 1968-2029286...
Simulating match 1968-2029287...
Simulating match 1968-2029288...
Simulating match 1968-2029289...
Simulating match 1968-2029290...
Simulating match 1968-2029291...
Simulating match 1968-2029292...
Simulating match 1968-2029293...
Simulating match 1968-2029294...
Simulating match 1968-2029295...
Simulating match 1968-2029296...
Simulating match 1968-2029297...
Simulating match 1968-2029298...
Simulat

In [43]:
all_tours.save_ranking()